In [1]:
from LLMPromptGenerator import LLMPromptGenerator

from audiocraft.models import MusicGen
from audiocraft.models import MultiBandDiffusion
from audiocraft.utils.notebook import display_audio

import math
import torchaudio
import torch
from audiocraft.utils.notebook import display_audio

/home/cayjobla/PAGES/.venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [1]:
text1 = """The dark figure streaming with fire raced towards them. The orcs yelled and poured over the stone gangways. Then Boromir raised his horn and blew. Loud the challenge rang and bellowed, like the shout of many throats under the cavernous roof. For a moment the orcs quailed and the fiery shadow halted. Then the echoes died as suddenly as a flame blown out by a dark wind, and the enemy advanced again.

‘Over the bridge!’ cried Gandalf, recalling his strength. ‘Fly! This is a foe beyond any of you. I must hold the narrow way. Fly!’ Aragorn and Boromir did not heed the command, but still held their ground, side by side, behind Gandalf at the far end of the bridge. The others halted just within the doorway at the hall's end, and turned, unable to leave their leader to face the enemy alone.

The Balrog reached the bridge. Gandalf stood in the middle of the span, leaning on the staff in his left hand, but in his other hand Glamdring gleamed, cold and white. His enemy halted again, facing him, and the shadow about it reached out like two vast wings. It raised the whip, and the thongs whined and cracked. Fire came from its nostrils. But Gandalf stood firm.

'You cannot pass,' he said. The orcs stood still, and a dead silence fell. 'I am a servant of the Secret Fire, wielder of the flame of Anor. You cannot pass. The dark fire will not avail you, flame of Udûn. Go back to the Shadow! You cannot pass.'

The Balrog made no answer. The fire in it seemed to die, but the darkness grew. It stepped forward slowly onto the bridge, and suddenly it drew itself up to a great height, and its wings were spread from wall to wall; but still Gandalf could be seen, glimmering in the gloom; he seemed small, and altogether alone: grey and bent, like a wizened tree before the onset of a storm.

From out of the shadow a red sword leaped flaming."""

In [5]:
text2 = """Glamdring glittered white in answer.

There was a ringing clash and a stab of white fire. The Balrog fell back and its sword flew up in molten fragments. The wizard swayed on the bridge, stepped back a pace, and then again stood still.

'You cannot pass!' he said.

With a bound the Balrog leaped full upon the bridge. Its whip whirled and hissed.

'He cannot stand alone!' cried Aragorn suddenly and ran back along the bridge. 'Elendil!' he shouted. 'I am with you, Gandalf!'

'Gondor!' cried Boromir and leaped after him."""

In [6]:
text3 = """At that moment Gandalf lifted his staff, and crying aloud he smote the bridge before him. The staff broke asunder and fell from his hand. A blinding sheet of white flame sprang up. The bridge cracked. Right at the Balrog's feet it broke, and the stone upon which it stood crashed into the gulf, while the rest remained, poised, quivering like a tongue of rock thrust out into emptiness.

With a terrible cry the Balrog fell forward, and its shadow plunged down and vanished. But even as it fell it swung its whip, and the thongs lashed and curled about the wizard's knees, dragging him to the brink. He staggered and fell, grasped vainly at the stone, and slid into the abyss. 'Fly, you fools!' he cried, and was gone.

The fires went out, and blank darkness fell. The Company stood rooted with horror staring into the pit. Even as Aragorn and Boromir came flying back, the rest of the bridge cracked and fell. With a cry Aragorn roused them.

'Come! I will lead you now!' he called. 'We must obey his last command. Follow me!'

They stumbled wildly up the great stairs beyond the door. Aragorn leading, Boromir at the rear. At the top was a wide echoing passage. Along this they fled. Frodo heard Sam at his side weeping, and then he found that he himself was weeping as he ran. Doom, doom, doom the drum-beats rolled behind, mournful now and slow; doom!
"""

In [7]:
extractor = LLMPromptGenerator()

In [8]:
text1_json = extractor.extract_info(text1)
text1_json

/home/cayjobla/PAGES/.venv/lib/python3.10/site-packages/transformers/generation/utils.py:1295: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in a future version. Please use and modify the model generation configuration (see https://huggingface.co/docs/transformers/generation_strategies#default-text-generation-configuration )
  warnings.warn(


'\n\n\n\n\n\n\n\n\n\n\n\n{\n"tone": "ominous",\n"intensity": "moderate",\n"instrumentation": "orchestral",\n"setting": "a dark and ominous underground cavern",\n"scene_description": "The dark figure streaming with fire raced towards them. The orcs yelled and poured over the stone gangways. Then Boromir raised his horn and blew. Loud the challenge rang and bellowed, like the shout of many throats under the cavernous roof. For a moment the orcs quailed and the fiery shadow halted. Then the echoes died as suddenly as a flame blown out by a dark wind, and the enemy advanced again.\',  "\n\n\n\n\n\n\n\n\n\n\n\n,"pitch": "low",\n"crescendo": true\n}\n\n\n\n\n\n\n\n\n\n\n\n'

In [9]:
text2_json = extractor.extract_info(text2)
text2_json

' {"tone": "ominous", "intensity": "high", "instrumentation": "ethereal", "setting": "a dark and foreboding landscape", "scene_description": "a massive stone bridge over a chasm, with a fierce Balrog guarding the far end", "pitch": "D minor", "crescendo": true}\n\n\n\n\n\n\n\n\n\n\n\n'

In [10]:
text3_json = extractor.extract_info(text3)
text3_json

' {"tone": "Serious", "intensity": "Loud", "instrumentation": "Orchestral", "setting": "Dark", "scene_description": "Dark, ominous background", "pitch": "Minor", "crescendo": false}\n\n\n\n\n\n\n\n\n\n\n\n'

In [11]:
import json

def save(text_json, filename):
    # Save the text1_json as a JSON file
    with open(filename, 'w') as file:
        json.dump(text_json, file)

In [13]:
save(text1_json, "text1.json")
save(text2_json, "text2.json")
save(text3_json, "text3.json")

## Generate Prompt

In [17]:
def info_to_prompt(json_str, SEP=', '):
    def get_element(value):
        if isinstance(value, list):
            return str(random.choice(value))
        if isinstance(value, bool):
            return value
        return str(value)
    
    key_order = {'scene_description': '{}',
             'setting': '{} setting',
             'related music setting/music genre': '{} music setting',
             'description/adjectives of scene': '{} description',
             'tone': '{} tone',
             'intensity': '{} intensity',
             'tempo/intensity': '{} tempo/intensity',
             'instrumentation': '{} instrumentals',
            #  'transition': '{} transition',
             'pitch': '{} pitch',
             'crescendo': '{}'
             }

    bool_to_text = {'crescendo': {True: 'with crescendo', False: ''}
                }
    
    info = json.loads(json_str)
    info = {k.lower(): v for k, v in info.items()}
    prompt = ""
    
    for key, format_str in key_order.items():
        if key in info:
            val_str = get_element(info[key]) # (key, info[key])
            if isinstance(val_str, bool) and key in bool_to_text:
                val_str = bool_to_text[key][val_str]
            if val_str != "":
                if prompt != "":
                    prompt += SEP
                prompt += f"{format_str.format(val_str)}"

    return prompt

In [19]:
text1_prompt = info_to_prompt(text1_json)
text1_prompt

"The dark figure streaming with fire raced towards them. The orcs yelled and poured over the stone gangways. Then Boromir raised his horn and blew. Loud the challenge rang and bellowed, like the shout of many throats under the cavernous roof. For a moment the orcs quailed and the fiery shadow halted. Then the echoes died as suddenly as a flame blown out by a dark wind, and the enemy advanced again.',  , a dark and ominous underground cavern setting, ominous tone, moderate intensity, orchestral instrumentals, low pitch, with crescendo"

In [20]:
text2_prompt = info_to_prompt(text2_json)
text2_prompt

'a massive stone bridge over a chasm, with a fierce Balrog guarding the far end, a dark and foreboding landscape setting, ominous tone, high intensity, ethereal instrumentals, D minor pitch, with crescendo'

In [21]:
text3_prompt = info_to_prompt(text3_json)
text3_prompt

'Dark, ominous background, Dark setting, Serious tone, Loud intensity, Orchestral instrumentals, Minor pitch'

## Generation

In [40]:
class GenMusicFromPrompt:
    def __init__(self, model_name="facebook/musicgen-large", use_diffusion_decoder=False):
        self.model = MusicGen.from_pretrained(model_name)
        self.mbd = MultiBandDiffusion.get_mbd_musicgen() if use_diffusion_decoder else None
        self.song = None

    def __call__():
        self.display_audio()

    def set_generation_params(self, use_sampling=True, top_k=0, duration=60):
        self.model.set_generation_params(
            use_sampling=use_sampling,
            top_k=top_k,
            duration=duration
        )
    
    def generate(self, prompt, **kwargs):
        self.set_generation_params(**kwargs)

        output = model.generate(
            descriptions=[
                prompt
            ],
            progress=True, return_tokens=True
        )
        initial_song = output[0]

        self.song = initial_song
    
    def generate_continuation(self, prompt, prev_song_duration=2, sample_rate=32000, **kwargs):
        if self.song is None:
            self.generate(prompt)

        self.set_generation_params(**kwargs)

        # Get the last `prev_song_duration` seconds of the previous song
        prompt_waveform = self.song[..., -int(prev_song_duration * sample_rate):]

        # Generate the continuation
        continued_song = model.generate_continuation(prompt_waveform,  # Add batch dimension
                                            prompt_sample_rate=sample_rate,  # Use the generated sample rate
                                            progress=True, return_tokens=True, descriptions=[prompt])

    def display_audio(self):
        if self.song is not None:
            display_audio(self.song)
        else:
            raise ValueError("No song to display. Please generate a song first.")

In [30]:
USE_DIFFUSION_DECODER = False
model_name="facebook/musicgen-large"
duration=30
top_k=250
model = MusicGen.get_pretrained(model_name)
if USE_DIFFUSION_DECODER:
    mbd = MultiBandDiffusion.get_mbd_musicgen()

model.set_generation_params(
    use_sampling=True,
    top_k=top_k,
    duration=duration
)

/home/cayjobla/PAGES/.venv/lib/python3.10/site-packages/torch/nn/utils/weight_norm.py:30: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")


In [31]:
# def generate_music(model, prompt, use_diffusion_decoder=False, do_display_audio=True):

#     output = model.generate(
#         descriptions=[
#             prompt
#         ],
#         progress=True, return_tokens=True
#     )
#     initial_song = output[0]

#     if do_display_audio:
#         display_audio(initial_song, sample_rate=32000)

#     return initial_song

In [41]:
def generate_music(model, prompt, prompt_sr=32000, prev_song=None, prev_song_overlap=2):
    if prev_song is None: # If initial song
        output = model.generate(
            progress=True, return_tokens=True, descriptions=[prompt]
        )
        initial_song = output[0]
        return initial_song
    else: # If continuation
        trim_amount = int(prev_song_overlap * prompt_sr)
        prompt_waveform = prev_song[..., -trim_amount:]
        # Generate the continuation
        continued_song = model.generate_continuation(prompt_waveform,  # Add batch dimension
                                            prompt_sample_rate=prompt_sr,  # Use the generated sample rate
                                            progress=True, return_tokens=True, descriptions=[prompt])
        continued_song = continued_song[0][:, :, trim_amount:]
        combined_song = torch.cat([prev_song, continued_song], dim=-1)
        return combined_song

In [37]:
initial_song = generate_music(model, text1_prompt)
display_audio(initial_song, sample_rate=32000)

In [42]:
song = generate_music(model, text2_prompt, prev_song=initial_song)
song = generate_music(model, text3_prompt, prev_song=song)
display_audio(song, sample_rate=32000)

## Left to work on

#### Before Midterm
* Metric for generated music - What is good?
* Look at generation times vs quality (Facebook model - Is live generation feasible?)

#### After Midterm
* Modify the LLM class to pass in a giant text file, batch, and generate json
* Pipeline the LLM and GenMusic class in a pipeline class
* Prompt engineering
* Fun: Karaoke interface 
